# Fetching Data

In [1]:
import ccxt
import pandas as pd
from datetime import datetime

# Initialize the Indodax exchange
exchange = ccxt.indodax()

# Define the trading pair and timeframe
symbol = 'USDT/IDR'  # Example: USDT to Indonesian Rupiah
timeframe = '1d'     # Supported timeframes: '1m', '5m', '15m', '1h', '1d', etc.
limit = 5000     # Number of candles to fetch (max depends on the exchange)

# Fetch OHLCV data
ohlcv = exchange.fetch_ohlcv(symbol, timeframe, limit=limit)

# Convert to DataFrame
columns = ['date', 'open', 'high', 'low', 'close', 'volume']
data = [
    [datetime.utcfromtimestamp(c[0] / 1000).strftime('%Y-%m-%d %H:%M:%S'), *c[1:]]
    for c in ohlcv
]
indodax_df = pd.DataFrame(data, columns=columns)

# Ensure 'date' column is in datetime format
indodax_df['date'] = pd.to_datetime(indodax_df['date'])

# Convert from UTC to Bali time (UTC+8)
indodax_df['date'] = indodax_df['date'] + pd.Timedelta(hours=8)

indodax_df = indodax_df.tail(len(indodax_df))

# Print the DataFrame
indodax_df

date     open     high      low    close        volume
0    2018-08-24 08:00:00  14600.0  19988.0  14506.0  14527.0  3.486209e+05
1    2018-08-25 08:00:00  14527.0  14615.0  14511.0  14550.0  1.235815e+05
2    2018-08-26 08:00:00  14551.0  14650.0  14551.0  14570.0  4.789076e+04
3    2018-08-27 08:00:00  14570.0  14640.0  14524.0  14550.0  6.555274e+04
4    2018-08-28 08:00:00  14550.0  14589.0  14536.0  14550.0  1.373922e+05
...                  ...      ...      ...      ...      ...           ...
2298 2024-12-08 08:00:00  15803.0  15908.0  15801.0  15821.0  5.488245e+06
2299 2024-12-09 08:00:00  15817.0  16134.0  15805.0  16055.0  1.126483e+07
2300 2024-12-10 08:00:00  16054.0  16054.0  15900.0  15965.0  1.159106e+07
2301 2024-12-11 08:00:00  15966.0  16023.0  15954.0  15954.0  1.088197e+07
2302 2024-12-12 08:00:00  15954.0  15960.0  15910.0  15929.0  1.601729e+06

[2303 rows x 6 columns]

# Data Exploration

In [2]:
indodax_df

date     open     high      low    close        volume
0    2018-08-24 08:00:00  14600.0  19988.0  14506.0  14527.0  3.486209e+05
1    2018-08-25 08:00:00  14527.0  14615.0  14511.0  14550.0  1.235815e+05
2    2018-08-26 08:00:00  14551.0  14650.0  14551.0  14570.0  4.789076e+04
3    2018-08-27 08:00:00  14570.0  14640.0  14524.0  14550.0  6.555274e+04
4    2018-08-28 08:00:00  14550.0  14589.0  14536.0  14550.0  1.373922e+05
...                  ...      ...      ...      ...      ...           ...
2298 2024-12-08 08:00:00  15803.0  15908.0  15801.0  15821.0  5.488245e+06
2299 2024-12-09 08:00:00  15817.0  16134.0  15805.0  16055.0  1.126483e+07
2300 2024-12-10 08:00:00  16054.0  16054.0  15900.0  15965.0  1.159106e+07
2301 2024-12-11 08:00:00  15966.0  16023.0  15954.0  15954.0  1.088197e+07
2302 2024-12-12 08:00:00  15954.0  15960.0  15910.0  15929.0  1.601729e+06

[2303 rows x 6 columns]

In [3]:
check_1 = indodax_df.copy()

check_1 = check_1[['date','close']]

check_1['close_chg_pct'] = (check_1['close'].shift(-1) - check_1['close']) / check_1['close'] * 100

check_1.dropna(inplace=True)

check_1

date    close  close_chg_pct
0    2018-08-24 08:00:00  14527.0       0.158326
1    2018-08-25 08:00:00  14550.0       0.137457
2    2018-08-26 08:00:00  14570.0      -0.137268
3    2018-08-27 08:00:00  14550.0       0.000000
4    2018-08-28 08:00:00  14550.0       0.453608
...                  ...      ...            ...
2297 2024-12-07 08:00:00  15803.0       0.113902
2298 2024-12-08 08:00:00  15821.0       1.479047
2299 2024-12-09 08:00:00  16055.0      -0.560573
2300 2024-12-10 08:00:00  15965.0      -0.068901
2301 2024-12-11 08:00:00  15954.0      -0.156701

[2302 rows x 3 columns]

In [4]:
import pandas as pd

# Assuming 'df' is the DataFrame containing your data
# Filter positive and negative values
positive_chg = check_1[check_1['close_chg_pct'] > 0]['close_chg_pct']
negative_chg = check_1[check_1['close_chg_pct'] < 0]['close_chg_pct']

# Calculate statistics
positive_stats = {
    'max': positive_chg.max(),
    'min': positive_chg.min(),
    'avg': positive_chg.mean(),
    'median': positive_chg.median()
}

negative_stats = {
    'max': negative_chg.max(),
    'min': negative_chg.min(),
    'avg': negative_chg.mean(),
    'median': negative_chg.median()
}

positive_stats, negative_stats

({'max': 6.368814769061835,
  'min': 0.006285355122564425,
  'avg': 0.44086281195758104,
  'median': 0.2599227256761504},
 {'max': -0.006228589224540642,
  'min': -3.68404014244092,
  'avg': -0.4437868538590375,
  'median': -0.30462651519959383})

In [5]:
# Count total rows excluding NaN
total_rows = check_1['close_chg_pct'].notna().sum()

# Count rows where 'close_chg_pct' >= 0
positive_or_zero_count = (check_1['close_chg_pct'] >= 0).sum()

# Calculate percentage
percentage_positive_or_zero = (positive_or_zero_count / total_rows) * 100

print(f"Percentage of 'close_chg_pct' >= 0: {percentage_positive_or_zero:.2f}%")

Percentage of 'close_chg_pct' >= 0: 52.26%


# Clean + Features Engineering

In [19]:
# Extracting features from minute data
df_base = indodax_df.copy()

# Calcualte daily change
df_base['close_chg_pct'] = (df_base['close'].shift(-1) - df_base['close']) / df_base['close'] * 100

# Create target flag
df_base['target_flag'] = df_base['close_chg_pct'].apply(
    lambda x: 1 if x >= 0.1 else (-1 if x <= -0.1 else 0)
)

df_base.dropna(inplace=True)

df_base = df_base.drop(columns=['close_chg_pct'])

df_base


date     open     high      low    close        volume  \
0    2018-08-24 08:00:00  14600.0  19988.0  14506.0  14527.0  3.486209e+05   
1    2018-08-25 08:00:00  14527.0  14615.0  14511.0  14550.0  1.235815e+05   
2    2018-08-26 08:00:00  14551.0  14650.0  14551.0  14570.0  4.789076e+04   
3    2018-08-27 08:00:00  14570.0  14640.0  14524.0  14550.0  6.555274e+04   
4    2018-08-28 08:00:00  14550.0  14589.0  14536.0  14550.0  1.373922e+05   
...                  ...      ...      ...      ...      ...           ...   
2297 2024-12-07 08:00:00  15831.0  15907.0  15801.0  15803.0  5.720112e+06   
2298 2024-12-08 08:00:00  15803.0  15908.0  15801.0  15821.0  5.488245e+06   
2299 2024-12-09 08:00:00  15817.0  16134.0  15805.0  16055.0  1.126483e+07   
2300 2024-12-10 08:00:00  16054.0  16054.0  15900.0  15965.0  1.159106e+07   
2301 2024-12-11 08:00:00  15966.0  16023.0  15954.0  15954.0  1.088197e+07   

      target_flag  
0               1  
1               1  
2              -1  
3               0  
4               1  
...           ...  
2297            1  
2298            1  
2299           -1  
2300            0  
2301           -1  

[2302 rows x 7 columns]

In [20]:
# Assuming df_base is your DataFrame
target_counts = df_base['target_flag'].value_counts(normalize=True) * 100
print(target_counts)

target_flag
 1    37.706342
-1    37.141616
 0    25.152042
Name: proportion, dtype: float64


# Logistic Regression

In [ ]:
import time
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, f1_score, accuracy_score

# Separate df into features and target
features_df = df_base.drop(['date', 'target_flag'], axis=1)
target_df = df_base['target_flag']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1  # Number of rows to predict
gap = 1              # Gap (number of rows to skip after each window)
max_windows = 50     # Maximum number of windows to process
set_limit = False    # Set this to False to process all windows

# List of window sizes
# window_sizes = list(range(50, 2000, 100))
window_sizes = [500]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:
    # Initiate lists to store training metrics
    train_accuracies = []
    train_f1_scores = []
    train_roc_auc_scores = []
    
    # List to store validation metrics
    validation_preds = []
    validation_true = []

    # Total time tracking
    total_window_times = 0

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:
        if window_number % 500 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        # Normalize training data
        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using training statistics
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time
        start_time = time.time()

        # Initialize and fit the Logistic Regression model
        model = LogisticRegression(max_iter=1000)
        model.fit(X_train_normalized, y_train)

        # Training metrics
        y_train_pred = model.predict(X_train_normalized)
        train_accuracy = accuracy_score(y_train, y_train_pred)
        train_f1 = f1_score(y_train, y_train_pred)
        train_roc_auc = roc_auc_score(y_train, model.predict_proba(X_train_normalized)[:, 1])

        train_accuracies.append(train_accuracy)
        train_f1_scores.append(train_f1)
        train_roc_auc_scores.append(train_roc_auc)

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Record predictions and true values for validation
        validation_preds.extend(y_pred_val)
        validation_true.extend(y_val)

        # Track the end time
        end_time = time.time()
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to total time

        # Move to the next window based on the gap
        window_number += gap

    # Calculate average training metrics
    avg_train_accuracy = np.mean(train_accuracies)
    avg_train_f1 = np.mean(train_f1_scores)
    avg_train_roc_auc = np.mean(train_roc_auc_scores)

    # Calculate validation metrics
    validation_accuracy = accuracy_score(validation_true, validation_preds)
    validation_f1 = f1_score(validation_true, validation_preds)
    validation_roc_auc = roc_auc_score(validation_true, validation_preds)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_train_accuracy': avg_train_accuracy,
        'avg_train_f1': avg_train_f1,
        'avg_train_roc_auc': avg_train_roc_auc,
        'validation_accuracy': validation_accuracy,
        'validation_f1': validation_f1,
        'validation_roc_auc': validation_roc_auc,
    })

    # Print results for the current window size
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average Train Accuracy: {avg_train_accuracy:.3f} | Average Train F1: {avg_train_f1:.3f} | Average Train ROC-AUC: {avg_train_roc_auc:.3f}')
    print(f'Validation Accuracy: {validation_accuracy:.3f} | Validation F1: {validation_f1:.3f} | Validation ROC-AUC: {validation_roc_auc:.3f}')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

## Multi Class

In [21]:
import time
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, confusion_matrix

# Separate df into features and target
features_df = df_base.drop(['date', 'target_flag'], axis=1)
target_df = df_base['target_flag']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1  # Number of rows to predict
gap = 1              # Gap (number of rows to skip after each window)
max_windows = 50     # Maximum number of windows to process
set_limit = False    # Set this to False to process all windows

# List of window sizes
window_sizes = [50, 100, 200, 500, 1000, 2000]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:
    # Initiate lists to store training metrics
    train_accuracies = []
    train_f1_scores = []

    # List to store validation metrics
    validation_preds = []
    validation_true = []

    # Total time tracking
    total_window_times = 0

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:
        if window_number % 500 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        # Normalize training data
        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using training statistics
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time
        start_time = time.time()

        # Initialize and fit the Logistic Regression model for multi-class classification
        model = LogisticRegression(max_iter=1000, multi_class='multinomial', solver='lbfgs')
        model.fit(X_train_normalized, y_train)

        # Training metrics
        y_train_pred = model.predict(X_train_normalized)
        train_accuracy = accuracy_score(y_train, y_train_pred)

        # Generate confusion matrix and calculate F1 score for training data
        cm_train = confusion_matrix(y_train, y_train_pred)
        train_f1 = 0
        for i in range(cm_train.shape[0]):
            tp = cm_train[i, i]
            fp = cm_train[:, i].sum() - tp
            fn = cm_train[i, :].sum() - tp
            precision = tp / (tp + fp) if tp + fp > 0 else 0
            recall = tp / (tp + fn) if tp + fn > 0 else 0
            f1 = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0
            train_f1 += f1
        train_f1 /= cm_train.shape[0]  # Macro F1 score

        train_accuracies.append(train_accuracy)
        train_f1_scores.append(train_f1)

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Record predictions and true values for validation
        validation_preds.extend(y_pred_val)
        validation_true.extend(y_val)

        # Track the end time
        end_time = time.time()
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to total time

        # Move to the next window based on the gap
        window_number += gap

    # Calculate average training metrics
    avg_train_accuracy = np.mean(train_accuracies)
    avg_train_f1 = np.mean(train_f1_scores)

    # Calculate validation metrics
    cm_val = confusion_matrix(validation_true, validation_preds)
    validation_f1 = 0
    for i in range(cm_val.shape[0]):
        tp = cm_val[i, i]
        fp = cm_val[:, i].sum() - tp
        fn = cm_val[i, :].sum() - tp
        precision = tp / (tp + fp) if tp + fp > 0 else 0
        recall = tp / (tp + fn) if tp + fn > 0 else 0
        f1 = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0
        validation_f1 += f1
    validation_f1 /= cm_val.shape[0]  # Macro F1 score

    validation_accuracy = accuracy_score(validation_true, validation_preds)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_train_accuracy': avg_train_accuracy,
        'avg_train_f1': avg_train_f1,
        'validation_accuracy': validation_accuracy,
        'validation_f1': validation_f1,
    })

    # Print results for the current window size
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average Train Accuracy: {avg_train_accuracy:.3f} | Average Train F1: {avg_train_f1:.3f}')
    print(f'Validation Accuracy: {validation_accuracy:.3f} | Validation F1: {validation_f1:.3f}')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Processing window 0 of 2251
Processing window 500 of 2251
Processing window 1000 of 2251
Processing window 1500 of 2251
Processing window 2000 of 2251
Window size [50] | Time Elapsed: 8.962 seconds
Average Train Accuracy: 0.550 | Average Train F1: 0.423
Validation Accuracy: 0.407 | Validation F1: 0.407
Processing window 0 of 2201
Processing window 500 of 2201
Processing window 1000 of 2201
Processing window 1500 of 2201
Processing window 2000 of 2201
Window size [100] | Time Elapsed: 9.985 seconds
Average Train Accuracy: 0.509 | Average Train F1: 0.382
Validation Accuracy: 0.416 | Validation F1: 0.417
Processing window 0 of 2101
Processing window 500 of 2101
Processing window 1000 of 2101
Processing window 1500 of 2101
Processing window 2000 of 2101
Window size [200] | Time Elapsed: 11.034 seconds
Average Train Accuracy: 0.482 | Average Train F1: 0.350
Validation Accuracy: 0.430 | Validation F1: 0.428
Processing window 0 of 1801
Processing window 500 of 1801
Processing window 1000 of 1

window_size  avg_train_accuracy  avg_train_f1  validation_accuracy  \
0           50            0.549542      0.422765             0.406930   
1          100            0.508778      0.382467             0.416174   
2          200            0.482442      0.350496             0.429795   
3          500            0.459067      0.346965             0.425875   
4         1000            0.448769      0.377898             0.383551   
5         2000            0.428527      0.424973             0.348837   

   validation_f1  
0       0.406805  
1       0.417086  
2       0.427528  
3       0.422774  
4       0.381808  
5       0.330744

## Random Split

In [22]:
import time
import numpy as np
import pandas as pd
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.model_selection import train_test_split

# Separate df into features and target
features_df = df_base.drop(['date', 'target_flag'], axis=1)
target_df = df_base['target_flag']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Set the seed for reproducibility
np.random.seed(42)

# Specify a list of train-test proportions to evaluate
proportions = [0.5, 0.6, 0.7, 0.8, 0.9]  # e.g., 50% train, 50% test, etc.

# List to store results
results = []

# Loop through each train-test proportion
for train_size in proportions:
    # Split the data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(
        X, y, train_size=train_size, random_state=42, stratify=y
    )

    # Normalize training data
    X_train_mean = np.mean(X_train, axis=0)
    X_train_std = np.std(X_train, axis=0)
    X_train_normalized = (X_train - X_train_mean) / X_train_std

    # Normalize testing data using training statistics
    X_test_normalized = (X_test - X_train_mean) / X_train_std

    # Start timing the training process
    start_time = time.time()

    # Initialize and fit the Logistic Regression model for multi-class classification
    model = LogisticRegression(max_iter=1000, multi_class='multinomial', solver='lbfgs')
    model.fit(X_train_normalized, y_train)

    # Training metrics
    y_train_pred = model.predict(X_train_normalized)
    train_accuracy = accuracy_score(y_train, y_train_pred)

    # Generate confusion matrix and calculate F1 score for training data
    cm_train = confusion_matrix(y_train, y_train_pred)
    train_f1 = 0
    for i in range(cm_train.shape[0]):
        tp = cm_train[i, i]
        fp = cm_train[:, i].sum() - tp
        fn = cm_train[i, :].sum() - tp
        precision = tp / (tp + fp) if tp + fp > 0 else 0
        recall = tp / (tp + fn) if tp + fn > 0 else 0
        f1 = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0
        train_f1 += f1
    train_f1 /= cm_train.shape[0]  # Macro F1 score

    # Testing metrics
    y_test_pred = model.predict(X_test_normalized)
    test_accuracy = accuracy_score(y_test, y_test_pred)

    # Generate confusion matrix and calculate F1 score for testing data
    cm_test = confusion_matrix(y_test, y_test_pred)
    test_f1 = 0
    for i in range(cm_test.shape[0]):
        tp = cm_test[i, i]
        fp = cm_test[:, i].sum() - tp
        fn = cm_test[i, :].sum() - tp
        precision = tp / (tp + fp) if tp + fp > 0 else 0
        recall = tp / (tp + fn) if tp + fn > 0 else 0
        f1 = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0
        test_f1 += f1
    test_f1 /= cm_test.shape[0]  # Macro F1 score

    # End timing the training process
    end_time = time.time()
    elapsed_time = end_time - start_time

    # Store the results
    results.append({
        'train_size': train_size,
        'test_size': 1 - train_size,
        'train_accuracy': train_accuracy,
        'train_f1': train_f1,
        'test_accuracy': test_accuracy,
        'test_f1': test_f1,
        'elapsed_time': elapsed_time
    })

    # Print results for the current proportion
    print(f'Train size: {train_size:.2f} | Test size: {1 - train_size:.2f}')
    print(f'Training Accuracy: {train_accuracy:.3f} | Training F1: {train_f1:.3f}')
    print(f'Testing Accuracy: {test_accuracy:.3f} | Testing F1: {test_f1:.3f}')
    print(f'Time Elapsed: {elapsed_time:.3f} seconds')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Train size: 0.50 | Test size: 0.50
Training Accuracy: 0.415 | Training F1: 0.394
Testing Accuracy: 0.445 | Testing F1: 0.430
Time Elapsed: 0.014 seconds
Train size: 0.60 | Test size: 0.40
Training Accuracy: 0.426 | Training F1: 0.410
Testing Accuracy: 0.444 | Testing F1: 0.431
Time Elapsed: 0.015 seconds
Train size: 0.70 | Test size: 0.30
Training Accuracy: 0.436 | Training F1: 0.424
Testing Accuracy: 0.430 | Testing F1: 0.421
Time Elapsed: 0.016 seconds
Train size: 0.80 | Test size: 0.20
Training Accuracy: 0.425 | Training F1: 0.416
Testing Accuracy: 0.403 | Testing F1: 0.395
Time Elapsed: 0.017 seconds
Train size: 0.90 | Test size: 0.10
Training Accuracy: 0.418 | Training F1: 0.408
Testing Accuracy: 0.416 | Testing F1: 0.402
Time Elapsed: 0.021 seconds


train_size  test_size  train_accuracy  train_f1  test_accuracy   test_f1  \
0         0.5        0.5        0.415291  0.394347       0.444831  0.429756   
1         0.6        0.4        0.425778  0.410438       0.444083  0.430614   
2         0.7        0.3        0.435754  0.424378       0.429812  0.420941   
3         0.8        0.2        0.424769  0.416158       0.403471  0.394730   
4         0.9        0.1        0.418155  0.408433       0.415584  0.401598   

   elapsed_time  
0      0.013774  
1      0.015333  
2      0.015826  
3      0.017246  
4      0.020933

# Random Forests

In [15]:
import time
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import roc_auc_score, f1_score, accuracy_score

# Separate df into features and target
features_df = df_base.drop(['date', 'target_flag'], axis=1)
target_df = df_base['target_flag']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1  # Number of rows to predict
gap = 1              # Gap (number of rows to skip after each window)
max_windows = 500     # Maximum number of windows to process
set_limit = False    # Set this to False to process all windows

# List of window sizes
# window_sizes = list(range(1200, 1401, 10))
window_sizes = [500]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:
    # Initiate lists to store training metrics
    train_accuracies = []
    train_f1_scores = []
    train_roc_auc_scores = []
    
    # List to store validation metrics
    validation_preds = []
    validation_true = []

    # Total time tracking
    total_window_times = 0

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:
        if window_number % 500 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        # Normalize training data
        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using training statistics
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time
        start_time = time.time()

        # Initialize and fit the Logistic Regression model
        model = RandomForestClassifier(n_estimators=40, random_state=42)
        model.fit(X_train_normalized, y_train)

        # Training metrics
        y_train_pred = model.predict(X_train_normalized)
        train_accuracy = accuracy_score(y_train, y_train_pred)
        train_f1 = f1_score(y_train, y_train_pred)
        train_roc_auc = roc_auc_score(y_train, model.predict_proba(X_train_normalized)[:, 1])

        train_accuracies.append(train_accuracy)
        train_f1_scores.append(train_f1)
        train_roc_auc_scores.append(train_roc_auc)

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Record predictions and true values for validation
        validation_preds.extend(y_pred_val)
        validation_true.extend(y_val)

        # Track the end time
        end_time = time.time()
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to total time

        # Move to the next window based on the gap
        window_number += gap

    # Calculate average training metrics
    avg_train_accuracy = np.mean(train_accuracies)
    avg_train_f1 = np.mean(train_f1_scores)
    avg_train_roc_auc = np.mean(train_roc_auc_scores)

    # Calculate validation metrics
    validation_accuracy = accuracy_score(validation_true, validation_preds)
    validation_f1 = f1_score(validation_true, validation_preds)
    validation_roc_auc = roc_auc_score(validation_true, validation_preds)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_train_accuracy': avg_train_accuracy,
        'avg_train_f1': avg_train_f1,
        'avg_train_roc_auc': avg_train_roc_auc,
        'validation_accuracy': validation_accuracy,
        'validation_f1': validation_f1,
        'validation_roc_auc': validation_roc_auc,
    })

    # Print results for the current window size
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average Train Accuracy: {avg_train_accuracy:.3f} | Average Train F1: {avg_train_f1:.3f} | Average Train ROC-AUC: {avg_train_roc_auc:.3f}')
    print(f'Validation Accuracy: {validation_accuracy:.3f} | Validation F1: {validation_f1:.3f} | Validation ROC-AUC: {validation_roc_auc:.3f}')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Processing window 0 of 1800
Processing window 500 of 1800
Processing window 1000 of 1800
Processing window 1500 of 1800
Window size [500] | Time Elapsed: 147.662 seconds
Average Train Accuracy: 0.999 | Average Train F1: 0.999 | Average Train ROC-AUC: 1.000
Validation Accuracy: 0.501 | Validation F1: 0.546 | Validation ROC-AUC: 0.497


window_size  avg_train_accuracy  avg_train_f1  avg_train_roc_auc  \
0          500            0.999186      0.999217           0.999997   

   validation_accuracy  validation_f1  validation_roc_auc  
0             0.501111       0.546465             0.49677

## Multi Class

In [26]:
import time
import numpy as np
import pandas as pd
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, confusion_matrix

# Separate df into features and target
features_df = df_base.drop(['date', 'target_flag'], axis=1)
target_df = df_base['target_flag']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1  # Number of rows to predict
gap = 1              # Gap (number of rows to skip after each window)
max_windows = 50     # Maximum number of windows to process
set_limit = False    # Set this to False to process all windows

# List of window sizes
window_sizes = [50, 100, 200, 500, 1000, 2000]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:
    # Initiate lists to store training metrics
    train_accuracies = []
    train_f1_scores = []

    # List to store validation metrics
    validation_preds = []
    validation_true = []

    # Total time tracking
    total_window_times = 0

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:
        if window_number % 500 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        # Normalize training data
        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using training statistics
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time
        start_time = time.time()

        # Initialize and fit the Logistic Regression model for multi-class classification
        model = RandomForestClassifier(n_estimators=3, random_state=42)
        model.fit(X_train_normalized, y_train)

        # Training metrics
        y_train_pred = model.predict(X_train_normalized)
        train_accuracy = accuracy_score(y_train, y_train_pred)

        # Generate confusion matrix and calculate F1 score for training data
        cm_train = confusion_matrix(y_train, y_train_pred)
        train_f1 = 0
        for i in range(cm_train.shape[0]):
            tp = cm_train[i, i]
            fp = cm_train[:, i].sum() - tp
            fn = cm_train[i, :].sum() - tp
            precision = tp / (tp + fp) if tp + fp > 0 else 0
            recall = tp / (tp + fn) if tp + fn > 0 else 0
            f1 = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0
            train_f1 += f1
        train_f1 /= cm_train.shape[0]  # Macro F1 score

        train_accuracies.append(train_accuracy)
        train_f1_scores.append(train_f1)

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Record predictions and true values for validation
        validation_preds.extend(y_pred_val)
        validation_true.extend(y_val)

        # Track the end time
        end_time = time.time()
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to total time

        # Move to the next window based on the gap
        window_number += gap

    # Calculate average training metrics
    avg_train_accuracy = np.mean(train_accuracies)
    avg_train_f1 = np.mean(train_f1_scores)

    # Calculate validation metrics
    cm_val = confusion_matrix(validation_true, validation_preds)
    validation_f1 = 0
    for i in range(cm_val.shape[0]):
        tp = cm_val[i, i]
        fp = cm_val[:, i].sum() - tp
        fn = cm_val[i, :].sum() - tp
        precision = tp / (tp + fp) if tp + fp > 0 else 0
        recall = tp / (tp + fn) if tp + fn > 0 else 0
        f1 = (2 * precision * recall) / (precision + recall) if precision + recall > 0 else 0
        validation_f1 += f1
    validation_f1 /= cm_val.shape[0]  # Macro F1 score

    validation_accuracy = accuracy_score(validation_true, validation_preds)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_train_accuracy': avg_train_accuracy,
        'avg_train_f1': avg_train_f1,
        'validation_accuracy': validation_accuracy,
        'validation_f1': validation_f1,
    })

    # Print results for the current window size
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average Train Accuracy: {avg_train_accuracy:.3f} | Average Train F1: {avg_train_f1:.3f}')
    print(f'Validation Accuracy: {validation_accuracy:.3f} | Validation F1: {validation_f1:.3f}')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Processing window 0 of 2251
Processing window 500 of 2251
Processing window 1000 of 2251
Processing window 1500 of 2251
Processing window 2000 of 2251
Window size [50] | Time Elapsed: 10.733 seconds
Average Train Accuracy: 0.868 | Average Train F1: 0.854
Validation Accuracy: 0.405 | Validation F1: 0.397
Processing window 0 of 2201
Processing window 500 of 2201
Processing window 1000 of 2201
Processing window 1500 of 2201
Processing window 2000 of 2201
Window size [100] | Time Elapsed: 10.960 seconds
Average Train Accuracy: 0.879 | Average Train F1: 0.870
Validation Accuracy: 0.393 | Validation F1: 0.381
Processing window 0 of 2101
Processing window 500 of 2101
Processing window 1000 of 2101
Processing window 1500 of 2101
Processing window 2000 of 2101
Window size [200] | Time Elapsed: 11.542 seconds
Average Train Accuracy: 0.875 | Average Train F1: 0.866
Validation Accuracy: 0.380 | Validation F1: 0.373
Processing window 0 of 1801
Processing window 500 of 1801
Processing window 1000 of

window_size  avg_train_accuracy  avg_train_f1  validation_accuracy  \
0           50            0.867641      0.854179             0.405153   
1          100            0.879378      0.870228             0.392549   
2          200            0.874719      0.866376             0.379819   
3          500            0.866952      0.860308             0.368129   
4         1000            0.872828      0.869453             0.348194   
5         2000            0.870023      0.869189             0.388704   

   validation_f1  
0       0.397058  
1       0.381406  
2       0.372908  
3       0.365262  
4       0.346777  
5       0.354432

# GaussianNB

In [21]:
import time
import numpy as np
import pandas as pd
from sklearn.naive_bayes import GaussianNB
from sklearn.metrics import roc_auc_score, f1_score, accuracy_score

# Separate df into features and target
features_df = df_base.drop(['date', 'target_flag'], axis=1)
target_df = df_base['target_flag']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1  # Number of rows to predict
gap = 1              # Gap (number of rows to skip after each window)
max_windows = 500     # Maximum number of windows to process
set_limit = False    # Set this to False to process all windows

# List of window sizes
# window_sizes = list(range(1200, 1401, 10))
window_sizes = [1000]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:
    # Initiate lists to store training metrics
    train_accuracies = []
    train_f1_scores = []
    train_roc_auc_scores = []
    
    # List to store validation metrics
    validation_preds = []
    validation_true = []

    # Total time tracking
    total_window_times = 0

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:
        if window_number % 500 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        # Normalize training data
        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using training statistics
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time
        start_time = time.time()

        # Initialize and fit the Logistic Regression model
        model = GaussianNB()
        model.fit(X_train_normalized, y_train)

        # Training metrics
        y_train_pred = model.predict(X_train_normalized)
        train_accuracy = accuracy_score(y_train, y_train_pred)
        train_f1 = f1_score(y_train, y_train_pred)
        train_roc_auc = roc_auc_score(y_train, model.predict_proba(X_train_normalized)[:, 1])

        train_accuracies.append(train_accuracy)
        train_f1_scores.append(train_f1)
        train_roc_auc_scores.append(train_roc_auc)

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Record predictions and true values for validation
        validation_preds.extend(y_pred_val)
        validation_true.extend(y_val)

        # Track the end time
        end_time = time.time()
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to total time

        # Move to the next window based on the gap
        window_number += gap

    # Calculate average training metrics
    avg_train_accuracy = np.mean(train_accuracies)
    avg_train_f1 = np.mean(train_f1_scores)
    avg_train_roc_auc = np.mean(train_roc_auc_scores)

    # Calculate validation metrics
    validation_accuracy = accuracy_score(validation_true, validation_preds)
    validation_f1 = f1_score(validation_true, validation_preds)
    validation_roc_auc = roc_auc_score(validation_true, validation_preds)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_train_accuracy': avg_train_accuracy,
        'avg_train_f1': avg_train_f1,
        'avg_train_roc_auc': avg_train_roc_auc,
        'validation_accuracy': validation_accuracy,
        'validation_f1': validation_f1,
        'validation_roc_auc': validation_roc_auc,
    })

    # Print results for the current window size
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average Train Accuracy: {avg_train_accuracy:.3f} | Average Train F1: {avg_train_f1:.3f} | Average Train ROC-AUC: {avg_train_roc_auc:.3f}')
    print(f'Validation Accuracy: {validation_accuracy:.3f} | Validation F1: {validation_f1:.3f} | Validation ROC-AUC: {validation_roc_auc:.3f}')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Processing window 0 of 1300
Processing window 500 of 1300
Processing window 1000 of 1300
Window size [1000] | Time Elapsed: 6.001 seconds
Average Train Accuracy: 0.537 | Average Train F1: 0.633 | Average Train ROC-AUC: 0.551
Validation Accuracy: 0.530 | Validation F1: 0.567 | Validation ROC-AUC: 0.527


window_size  avg_train_accuracy  avg_train_f1  avg_train_roc_auc  \
0         1000            0.536778      0.632946           0.551039   

   validation_accuracy  validation_f1  validation_roc_auc  
0                 0.53       0.566974            0.526625

# XGBoost

In [22]:
import time
import numpy as np
import pandas as pd
from xgboost import XGBClassifier

# Separate df into features and target
features_df = df.drop(['date', 'next_close_change'], axis=1)
target_df = df['next_close_change']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1   # Number of rows to predict
gap = 1               # Gap (number of rows to skip after each window)
max_windows = 100      # Maximum number of windows to process
set_limit = False     # Set this to False to process all windows

# Define list of window sizes
# window_sizes = list(range(100, 1001, 100))
window_sizes = [600]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:

    # Initiate lists to store F1 scores and accuracies
    all_f1_scores = []
    accuracies = []
    total_window_times = 0  # Variable to store total time for all windows

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:

        if window_number % 1000 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data for prediction
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using the statistics from the training set
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time of the window processing
        start_time = time.time()

        # Initialize and fit the Logistic Regression model
        model = XGBClassifier(
            objective='binary:logistic',  # For binary classification
            n_estimators=100,  # Number of trees
            learning_rate=0.1,  # Learning rate
            max_depth=6,  # Maximum depth of each tree
            random_state=42,
            use_label_encoder=False)  # To suppress warnings about label encoding
        model.fit(X_train_normalized, y_train)  # Train without normalizing y_train

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Binary prediction and ground truth
        y_pred_binary_val = np.where(y_pred_val  == True, 1, 0)  # Binary prediction (1 if predicted value <= 0.03)
        y_binary_val = np.where(y_val == True, 1, 0)  # Binary ground truth (1 if actual value is True, else 0)


        # Calculate True Positives (TP), False Positives (FP), False Negatives (FN), and True Negatives (TN)
        TP = np.sum((y_pred_binary_val == 1) & (y_binary_val == 1))
        FP = np.sum((y_pred_binary_val == 1) & (y_binary_val == 0))
        FN = np.sum((y_pred_binary_val == 0) & (y_binary_val == 1))
        TN = np.sum((y_pred_binary_val == 0) & (y_binary_val == 0))

        # Calculate Precision and Recall safely
        precision = TP / (TP + FP) if (TP + FP) > 0 else 0  # Avoid division by zero
        recall = TP / (TP + FN) if (TP + FN) > 0 else 0  # Avoid division by zero

        # Calculate F1 Score safely
        f1 = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0

        # Calculate Accuracy
        accuracy = (TP + TN) / (TP + TN + FP + FN) if (TP + TN + FP + FN) > 0 else 0

        # Store the results
        all_f1_scores.append(f1)
        accuracies.append(accuracy)

        # Track the end time of the window processing
        end_time = time.time()

        # Calculate the time taken for this window
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to the total time

        # Move to the next window based on the gap
        window_number += gap
    
    # Calculate average F1 score and accuracy
    avg_f1_score = np.mean(all_f1_scores)
    avg_accuracy = np.mean(accuracies)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_f1_score': avg_f1_score,
        'avg_accuracy': avg_accuracy,
        'total_time': total_window_times
    })
    
    # Print results for the current window size with the new name
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average F1 Score: {avg_f1_score:.3f} | Average Accuracy: {avg_accuracy:.3f} %')
    print(f'===================================================================================')

# Convert the results into a DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Processing window 0 of 226


/home/ubuntu/.local/lib/python3.10/site-packages/xgboost/core.py:158: UserWarning: [05:14:11] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/home/ubuntu/.local/lib/python3.10/site-packages/xgboost/core.py:158: UserWarning: [05:14:44] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/home/ubuntu/.local/lib/python3.10/site-packages/xgboost/core.py:158: UserWarning: [05:15:17] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/home/ubuntu/.local/lib/python3.10/site-packages/xgboost/core.py:158: UserWarning: [05:15:50] WARNING: /workspace/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/home/ubuntu/.local/lib/python3.10/site-packages/xgboost/core.py:158: UserWarning: [05:16:24] WARNING: /workspace/sr

Window size [600] | Time Elapsed: 7709.709 seconds
Average F1 Score: 0.274 | Average Accuracy: 0.513 %


window_size  avg_f1_score  avg_accuracy  total_time
0          600      0.274336      0.513274  7709.70916

# LightGBM

In [19]:
import time
import numpy as np
import pandas as pd
from lightgbm import LGBMClassifier
from sklearn.metrics import roc_auc_score, f1_score, accuracy_score

# Separate df into features and target
features_df = df_h_features_filtered.drop(['date', 'close_movement'], axis=1)
target_df = df_h_features_filtered['close_movement']

# Convert to NumPy arrays
X = features_df.values
y = target_df.values

# Specify parameters for the sliding window approach
num_predictions = 1  # Number of rows to predict
gap = 1              # Gap (number of rows to skip after each window)
max_windows = 500     # Maximum number of windows to process
set_limit = False    # Set this to False to process all windows

# List of window sizes
# window_sizes = list(range(1200, 1401, 10))
window_sizes = [1000]

# List to store results
results = []

# Loop through each window size
for window_size in window_sizes:
    # Initiate lists to store training metrics
    train_accuracies = []
    train_f1_scores = []
    train_roc_auc_scores = []
    
    # List to store validation metrics
    validation_preds = []
    validation_true = []

    # Total time tracking
    total_window_times = 0

    # Calculate the number of windows based on dataset size
    num_windows = len(X) - window_size - num_predictions

    # Apply maximum window limit if set
    if set_limit:
        num_windows = min(num_windows, max_windows)

    # Loop through each sliding window with the gap applied
    window_number = 0
    while window_number < num_windows:
        if window_number % 500 == 0:
            print(f'Processing window {window_number} of {num_windows}')

        start = window_number
        end = start + window_size
        X_train = X[start:end]
        y_train = y[start:end]

        # Normalize training data
        X_train_mean = np.mean(X_train, axis=0)
        X_train_std = np.std(X_train, axis=0)
        X_train_normalized = (X_train - X_train_mean) / X_train_std

        # Prepare validation data
        X_val = X[end:end + num_predictions]
        y_val = y[end:end + num_predictions]

        # Normalize validation data using training statistics
        X_val_normalized = (X_val - X_train_mean) / X_train_std

        # Track the start time
        start_time = time.time()

        # Initialize and fit the Logistic Regression model
        model = LGBMClassifier(
            n_estimators=100,
            learning_rate=0.1,
            max_depth=50,  # No limit by default, can be adjusted
            random_state=42)  # To suppress warnings about label encoding
        model.fit(X_train_normalized, y_train)

        # Training metrics
        y_train_pred = model.predict(X_train_normalized)
        train_accuracy = accuracy_score(y_train, y_train_pred)
        train_f1 = f1_score(y_train, y_train_pred)
        train_roc_auc = roc_auc_score(y_train, model.predict_proba(X_train_normalized)[:, 1])

        train_accuracies.append(train_accuracy)
        train_f1_scores.append(train_f1)
        train_roc_auc_scores.append(train_roc_auc)

        # Predict on validation data
        y_pred_val = model.predict(X_val_normalized)
        
        # Record predictions and true values for validation
        validation_preds.extend(y_pred_val)
        validation_true.extend(y_val)

        # Track the end time
        end_time = time.time()
        window_time = end_time - start_time
        total_window_times += window_time  # Add the window time to total time

        # Move to the next window based on the gap
        window_number += gap

    # Calculate average training metrics
    avg_train_accuracy = np.mean(train_accuracies)
    avg_train_f1 = np.mean(train_f1_scores)
    avg_train_roc_auc = np.mean(train_roc_auc_scores)

    # Calculate validation metrics
    validation_accuracy = accuracy_score(validation_true, validation_preds)
    validation_f1 = f1_score(validation_true, validation_preds)
    validation_roc_auc = roc_auc_score(validation_true, validation_preds)

    # Store the results
    results.append({
        'window_size': window_size,
        'avg_train_accuracy': avg_train_accuracy,
        'avg_train_f1': avg_train_f1,
        'avg_train_roc_auc': avg_train_roc_auc,
        'validation_accuracy': validation_accuracy,
        'validation_f1': validation_f1,
        'validation_roc_auc': validation_roc_auc,
    })

    # Print results for the current window size
    print(f'Window size [{window_size}] | Time Elapsed: {total_window_times:.3f} seconds')
    print(f'Average Train Accuracy: {avg_train_accuracy:.3f} | Average Train F1: {avg_train_f1:.3f} | Average Train ROC-AUC: {avg_train_roc_auc:.3f}')
    print(f'Validation Accuracy: {validation_accuracy:.3f} | Validation F1: {validation_f1:.3f} | Validation ROC-AUC: {validation_roc_auc:.3f}')
    print(f'===================================================================================')

# Convert results to DataFrame for easy viewing
results_summary = pd.DataFrame(results)

# Display the results
results_summary

Processing window 0 of 15353
[LightGBM] [Info] Number of positive: 710, number of negative: 290
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003778 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 4931
[LightGBM] [Info] Number of data points in the train set: 1000, number of used features: 29
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.710000 -> initscore=0.895384
[LightGBM] [Info] Start training from score 0.895384
[LightGBM] [Info] Number of positive: 710, number of negative: 290
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000730 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4928
[LightGBM] [Info] Number of data points in the train set: 1000, number of used features: 29
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.710000 -> inits

window_size  avg_train_accuracy  avg_train_f1  avg_train_roc_auc  \
0         1000            0.998515      0.998792           0.999987   

   validation_accuracy  validation_f1  validation_roc_auc  
0             0.606136       0.700154            0.562593